# Name: Mohammad Javad Noroozi
# Student Number: 99102434
# Project

### import the necessary library

In [1]:
# !pip install pandas
# !pip install pyarrow

In [2]:
import json
import datetime
import random
import pandas as pd


In [3]:
import findspark
findspark.find()
findspark.init()
import pyspark
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, size
from pyspark.sql.streaming import DataStreamWriter
from pyspark.sql.functions import length
import findspark


# Create the Spark Session
from pyspark.sql import SparkSession

spark = SparkSession \
    .builder \
    .appName("Streaming Process Files") \
    .config("spark.streaming.stopGracefullyOnShutdown", True) \
    .master("local[*]") \
    .getOrCreate()

spark

24/02/06 02:20:13 WARN Utils: Your hostname, javad-IdeaPad-Gaming-3-15IAH7 resolves to a loopback address: 127.0.1.1; using 192.168.43.226 instead (on interface wlp0s20f3)
24/02/06 02:20:13 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
24/02/06 02:20:14 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
24/02/06 02:20:14 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.
24/02/06 02:20:14 WARN Utils: Service 'SparkUI' could not bind on port 4041. Attempting port 4042.


In [4]:

necessary_keys = [
    'tweet_type',
    'user', 
    'id',
    'created_at',
    'text',
    'in_reply_to_status_id_str', 'in_reply_to_user_id_str',
    'quoted_status', 'retweeted_status',
    "tweet_type",
    "view_count",
    "twitter_engagement_rate",
    "retweet_count",
    "reply_count",
    "quote_count",
    "influence",
    "impression_rate",
    "impression",
    "favorited",
    "favorite_count",
    "engagement_rate",
    "engagement",
    'entities',
    ]

exploded_keys = [
    'user.verified as verified', 
    'user.followers_count as followers_count', 
    'user.friends_count as friends_count', 
    'user.listed_count as listed_count', 
    'user.favourites_count as favourites_count', 
    'user.statuses_count as statuses_count', 
    'user.description as description', 
    'user.name as name', 
    'entities.hashtags as hashtags', 
    'id',
    'created_at',
    'text',
    'in_reply_to_status_id_str', 'in_reply_to_user_id_str',
    'quoted_status', 'retweeted_status',
    "tweet_type",
    "view_count",
    "twitter_engagement_rate",
    "retweet_count",
    "reply_count",
    "quote_count",
    "influence",
    "impression_rate",
    "impression",
    "favorited",
    "favorite_count",
    "engagement_rate",
    "engagement",
]

user_statistics_keys = [
    "name",
    "verified",
    "followers_count",
    "friends_count",
    "listed_count",
    "favourites_count",
    "statuses_count",
]

In [6]:
# To allow automatic schemaInference while reading
spark.conf.set("spark.sql.streaming.schemaInference", True)

file_path = "/home/javad/venvspark/notebooks/Project/databricks-datasets/structured-streaming/events"

# Create the streaming_df to read from input directory
streaming_df = spark.readStream\
    .format("json") \
    .option("maxFilesPerTrigger", 1) \
    .load(file_path)


exploded_df = streaming_df \
    .select(necessary_keys) 

flattened_df = exploded_df \
    .selectExpr(exploded_keys) 



# Define filtering conditions
filtered_streaming_df = flattened_df.filter(
    (col("followers_count") > 1000) &
    (col("statuses_count") > 500) &
    (length("description") > 20) &
    (length("text") > 20) &
    (size(col("hashtags")) < 5) &
    (col("tweet_type") != 'replied') &
    (col("quote_count") > 0) &  
    (col("view_count") < 10*col("friends_count")) &
    (col("retweet_count") < 10*col("quote_count")+10*col("reply_count")) &
    (col("reply_count") > 5) &
    (col("retweet_count") > 5)
).select(user_statistics_keys)

     
query: DataStreamWriter = filtered_streaming_df.writeStream\
        .outputMode("append")\
        .option("path", "data/output/device_data") \
        .option("checkpointLocation","checkpoint_dir") \
        .start()



24/02/06 02:23:11 WARN ResolveWriteToStream: spark.sql.adaptive.enabled is not supported in streaming DataFrames/Datasets and will be disabled.


24/02/06 02:23:12 WARN MemoryManager: Total allocation exceeds 95.00% (1,020,054,720 bytes) of heap memory
Scaling row group sizes to 95.00% for 8 writers
24/02/06 02:23:12 WARN MemoryManager: Total allocation exceeds 95.00% (1,020,054,720 bytes) of heap memory
Scaling row group sizes to 84.44% for 9 writers
24/02/06 02:23:12 WARN MemoryManager: Total allocation exceeds 95.00% (1,020,054,720 bytes) of heap memory
Scaling row group sizes to 76.00% for 10 writers
24/02/06 02:23:12 WARN MemoryManager: Total allocation exceeds 95.00% (1,020,054,720 bytes) of heap memory
Scaling row group sizes to 69.09% for 11 writers
24/02/06 02:23:12 WARN MemoryManager: Total allocation exceeds 95.00% (1,020,054,720 bytes) of heap memory
Scaling row group sizes to 63.33% for 12 writers
24/02/06 02:23:14 WARN MemoryManager: Total allocation exceeds 95.00% (1,020,054,720 bytes) of heap memory
Scaling row group sizes to 69.09% for 11 writers
24/02/06 02:23:14 WARN MemoryManager: Total allocation exceeds 95.

In [7]:
file_path = '/home/javad/venvspark/notebooks/Project/data/output/device_data'
df = pd.read_parquet(file_path, engine='pyarrow')
pd.set_option('display.max_rows', None)
df

name  verified  \
0                                       👑Golda Maccabi👑      True   
1                             Nazanin Afshin-Jam MacKay      True   
2                             Nasim Behrouz💎👑نسیم بهروز      True   
3                                          Suleman Khan     False   
4                                       Saeed.kooshafar     False   
5                                       Gheis Ghoreishi      True   
6                                      Kourosh Nazarian      True   
7                               👑 🩵𓄂𓆃 𝒔𝒂𝒓𝒂  🩵𓄂𓆃 👑🫡 🇺🇸     False   
8                                             گودگرل :/     False   
9                                            شراگیم زند      True   
10                                  مسافرى از لى لى پوت     False   
11                                               Loabat      True   
12                                                 حکیم     False   
13                                          𝐍𝐚𝐯𝐞𝐞𝐝 𝐊𝐡𝐚𝐧      True   
14                              👑 🩵𓄂𓆃 𝒔𝒂𝒓𝒂  🩵𓄂𓆃 👑🫡 🇺🇸     False   
15                                          احمد جانجان     False   
16                              👑 🩵𓄂𓆃 𝒔𝒂𝒓𝒂  🩵𓄂𓆃 👑🫡 🇺🇸     False   
17                           lilbit 🕊 #WomanLifeFreedom     False   
18                                       علی قاسمی 🇮🇷🇵🇸     False   
19                                         دربدر حرف حق     False   
20                                      👑Golda Maccabi👑      True   
21                                            Dr Samina     False   
22                                     Hamed Sarrafpour     False   
23                                        Faryad Khashm     False   
24                                        مصطفی شریفیان     False   
25                                  Lightroom999 ☼ 𓄂𓆃 𓃬     False   
26                                         داریوش معمار      True   
27                                            Shifa PTI     False   
28                                    Niflheim نیفلهایم     False   
29                                               Kenshi     False   
30                                          𝐍𝐚𝐯𝐞𝐞𝐝 𝐊𝐡𝐚𝐧      True   
31                                        sobhan.lens♦️     False   
32                                                 حکیم     False   
33                                     Mahmood 🇾🇪 yemen     False   
34                                          خان داداش 👑      True   
35                                       Aziz Khan Fb💙💯     False   
36                                             Anum Ali      True   
37                                     Hamed Sarrafpour     False   
38                                      Parinaz ‏Etesam     False   
39                                        Tayyaba Amjad     False   
40                                             𓄂کوهیار𓆃     False   
41                                               peyman     False   
42                                   Elyar Qaradağlı 🇦🇿     False   
43                                             Anum Ali      True   
44                                امیرآریان♕(طنزنوشت)𓃬☼     False   
45                                              Shobeir      True   
46                                              kamaran     False   
47                                        من نفرت انگیز     False   
48                                           Mariy2020     False   
49                                              هـلیـا‏     False   
50                                                Honey     False   
51                                      ٹیچر۔شمائلہ ڈار     False   
52                                         Suleman Khan     False   
53                                              Ario 𓄂✺      True   
54                                               Amir 🪶     False   
55                                           MehdiSadri     False   
56                                       Salman Durrani      True   
57                                             Mo